# Appendix 2 
This notebook is made as an suplementary documents as anwser sheet of exam two 

# Monte Carol Simulation

In [1]:
# Importing libraries
import pandas as pd
from numpy import *

# Libraries for plotting
import matplotlib.pyplot as plt
import cufflinks as cf
cf.set_config_file(offline=True)

# Set max row to 300
pd.set_option('display.max_rows', 300)

# 1. Compute Binary Option Value via Black Schole Model

In [2]:


# Import Libraries
from scipy.stats import norm
from math import exp, log, sqrt

# Assign values to parameters
S0 = 100.0  # Today's Stock Price
sigma = 0.2     # Vololity of 20%
r = 0.05    # Constant Risk-free rate of 1%
T = 1.0     # Time to Expiry (T-t)
E = 100.0   # Strike Price
# Compute d2 
d2 = (log(S0/E) + (r - 0.5*sigma**2) * T) / sigma*sqrt(T)

# Compute Binary Call Option Value acc. to Black Schole
BS_Call_Value = exp(-r * T) * norm.cdf(d2)
# Compute Binary Put Option Value
BS_Put_Value = exp(-r * T) * (1- norm.cdf(d2))

round(BS_Call_Value,6), round(BS_Put_Value,6)


(0.532325, 0.418905)

# 2. Compute Binary Option Value via Monte Carol Method 

In [3]:
# Import Libraries
import random # generate random number
from math import exp, sqrt

# Assign values to Parameters

S0 = 100.0    # Today's Stock Price
E = 100.0     # Strike Price
V = 0.2       # Volality of 20%
r = 0.05      # Constant Risk-free rate of 1%
T = 1.0       # Time to Expiry (T-t)
N= 100000     # Monte Carol Simulation Numbers

# Compute stock price via Euler_Maruyama Sechme
def Euler_Maruyama(S0,Sigma, r, T):
    ST = S0 * exp(T*(r-0.5*V**2)+ V*sqrt(T)* random.gauss(0,1.0))
    return ST 

# Define Heaviside binary option payoff function. 
# This name is after English mathematician Oliver Heaviside.
# Define binary call option payoff function 
def Heaviside(H):
    if H > 0:
        return 1.0
    else:
        return 0.0

Call_Payoff_Sum = 0.0 # Initialise Binary Call Option Payoff
Put_Payoff_Sum  =0.0  # Initialise Binary Put Option Payoff

#  Compute Call option Payoff by interating simulation numbers
for i in range(N):
    ST = Euler_Maruyama(S0, V, r, T) 
    Call_Payoff_Sum += Heaviside(ST-E)

#  Compute Put option Payoff by interating simulation numbers
for i in range(N):
    ST = Euler_Maruyama(S0, V, r, T) 
    Put_Payoff_Sum += Heaviside(E-ST) 

# compute option value
MC_Call_Value = exp(-r * T) * (Call_Payoff_Sum / float(N))
MC_Put_Value = exp(-r * T) * (Put_Payoff_Sum / float(N))

round(MC_Call_Value,6)  , round(MC_Put_Value,6)


(0.533364, 0.419502)

# 3. Simulate price paths

In [4]:
# Importing libraries
import pandas as pd
from numpy import *

# Libraries for plotting
import matplotlib.pyplot as plt
import cufflinks as cf
cf.set_config_file(offline=True)

# Set max row to 300
pd.set_option('display.max_rows', 300)

In [5]:
def simulate_path(ST, r, sigma, T, t, N):
    
    # Set the random seed for reproducibility
    # Same seed leads to the same set of random values
    random.seed(10000) 
 
    dt = T/t        # length of time interval  
    
    # Simulating 'n' asset price paths with 't' timesteps
    ST = zeros((t+1, N))
    ST[0] = 100

    for i in range(1, t+1):
        Phi = random.standard_normal(N)     # psuedo random numbers
        # This is Euler Maruyama Scheme
        ST[i] = ST[i-1] * exp((r - 0.5*sigma*sigma)*dt + sigma*sqrt(dt) * Phi) # vectorized operation per timesteps
        
    return ST


# 4.  Histogram of Simulated Paths

In [6]:
price_path = pd.DataFrame(simulate_path(100, 0.05, 0.20, 1, 252, 100000))
price_path.shape

(253, 100000)

In [7]:
# Plot the histogram of the simulated price path at maturity
price_path.iloc[-1].iplot(kind='histogram', title= 'Simulated Geometric Brownian Motion at Maturity', bins=100)

In [8]:
# Verify the generated price paths 
price_path.tail()

0          1           2          3          4           5      \
248  122.744116  73.726256  130.300175  85.189213  97.832185  145.078927   
249  123.481394  75.683974  129.657857  83.829975  98.647390  145.796634   
250  120.425574  74.540613  129.857575  83.173612  99.329872  145.326902   
251  121.041764  74.274111  130.494232  82.587781  97.291661  143.060354   
252  119.614091  76.158298  129.412627  81.065594  98.140474  143.715903   

         6           7           8          9      ...       99990  \
248  80.238957  115.570249  146.166446  92.363360  ...  115.268251   
249  79.768302  115.431777  143.233227  92.761168  ...  113.820214   
250  79.856524  114.917017  145.739873  94.496627  ...  112.924580   
251  80.695230  111.935555  147.320979  95.150662  ...  112.504629   
252  82.260569  111.930403  149.914686  94.996926  ...  113.464643   

          99991      99992       99993      99994       99995      99996  \
248   97.785460  77.997978  125.746500  66.248592  101.359439  98.117755   
249   98.806408  78.179687  123.540823  67.150401  102.689798  97.286120   
250  100.028868  79.705226  123.337220  67.575219  102.027625  97.845233   
251   99.577606  80.501443  122.850952  66.989567  102.092763  98.906659   
252   99.783934  81.659347  124.103865  66.765986  102.196988  98.788117   

          99997       99998      99999  
248  106.427116  116.403264  88.053283  
249  107.246420  117.029213  88.093302  
250  105.380055  119.285472  90.154848  
251  107.483858  119.385760  86.898010  
252  107.454989  122.229576  86.254176  

[5 rows x 100000 columns]

# 5.Visualization of Simulated Path

In [9]:
# Plot simulated price paths 
price_path.iloc[:,:100].iplot(title='Simulated Geometric Brownian Motion Asset Paths', xTitle='Time Steps', yTitle='Asset Price')